In [ ]:
from transformers import DebertaTokenizer, DebertaForSequenceClassification
from transformers import pipeline

save_path = '/home/raj.tomar/Downloads/MGT/experiments/fine-tuned-deberta/'
model = DebertaForSequenceClassification.from_pretrained(save_path)
tokenizer = DebertaTokenizer.from_pretrained(save_path)

classifier = pipeline('text-classification', model=model, tokenizer=tokenizer)


In [ ]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer_essay = AutoTokenizer.from_pretrained("ngocminhta/RoBERTa-MGT-Test")
model_essay = AutoModelForSequenceClassification.from_pretrained("ngocminhta/RoBERTa-MGT-Test")

classifier_essay = pipeline('text-classification', model=model_essay, tokenizer=tokenizer_essay)

In [ ]:
classifier_essay("The Impact of Social Media on Society In the contemporary world, social media has become an integral part of daily life, shaping how people communicate, interact, and share information. Platforms such as Facebook, Twitter, Instagram, and TikTok have transformed the landscape of communication, offering unprecedented access to information and connectivity. While social media presents numerous benefits, it also poses significant challenges and concerns. This essay explores the multifaceted impact of social media on society, examining both its positive contributions and its potential drawbacks. Positive Impacts One of the most notable positive impacts of social media is its ability to foster connectivity and communication. Social media platforms allow individuals to maintain relationships with friends and family members, regardless of geographical barriers. For instance, expatriates can stay in touch with loved ones back home, and people can form global communities based on shared interests. This enhanced connectivity has contributed to a more interconnected and empathetic world. Moreover, social media serves as a powerful tool for information dissemination and awareness. News outlets and organizations use these platforms to reach a broader audience, delivering real-time updates on global events. During crises, such as natural disasters or political upheavals, social media can facilitate the rapid spread of crucial information, aiding in disaster response and mobilizing support. Additionally, social media has played a significant role in social and political movements, enabling activists to organize, raise awareness, and advocate for change. The educational potential of social media is another significant benefit. Platforms like YouTube, LinkedIn, and Twitter offer a wealth of educational content, ranging from instructional videos to professional development resources. Educators and institutions leverage social media to engage with students, share knowledge, and foster collaborative learning environments. This democratization of information has made education more accessible to people worldwide. Negative Impacts Despite its many advantages, social media also has several negative implications. One of the most pressing concerns is its impact on mental health. Studies have shown that excessive use of social media can lead to feelings of anxiety, depression, and loneliness. The constant comparison with others' curated online personas can create unrealistic expectations and contribute to low self-esteem. Additionally, cyberbullying and online harassment have become prevalent issues, particularly among young people, exacerbating mental health problems. Another significant issue is the spread of misinformation and fake news. Social media platforms, with their vast reach and rapid information dissemination, are often used to spread false or misleading content. This phenomenon can have serious consequences, such as influencing public opinion, exacerbating political polarization, and undermining trust in institutions. The algorithms that drive social media often prioritize sensational and controversial content, further amplifying the spread of misinformation. Privacy concerns are also paramount in the discussion of social media's impact. The collection and use of personal data by social media companies raise significant ethical and security issues. Users often unknowingly share vast amounts of personal information, which can be exploited for targeted advertising, data breaches, and surveillance. The lack of stringent regulatory frameworks exacerbates these concerns, leaving users vulnerable to privacy violations. Conclusion In conclusion, social media has profoundly influenced modern society, offering both remarkable benefits and substantial challenges. It has revolutionized communication, provided educational opportunities, and empowered social and political movements. However, it also poses significant risks to mental health, facilitates the spread of misinformation, and raises critical privacy concerns. As social media continues to evolve, it is essential to strike a balance between leveraging its positive aspects and mitigating its negative impacts. Policymakers, educators, and users must work collaboratively to ensure that social media remains a force for good in society, fostering a connected, informed, and resilient global community.")

In [ ]:

classifier("We have analyzed the HI aperture synthesis image of the Large Magellanic\nCloud (LMC), using an objective and quantitative measure of topology to\nunderstand the HI distribution hosting a number of holes and clumps of various\nsizes in the medium.") 

In [ ]:
# from huggingface_hub import HfFolder, notebook_login
# notebook_login()

In [ ]:
import gradio as gr

def update(name, uploaded_file, radio_type):
    if uploaded_file is not None:
        return f"{name}, you uploaded a file named {uploaded_file.name}."
    else:
        if radio_type == 'Student Essay':
            return classifier(name)[0]['label']
        else:
            return "Hold on!"

with gr.Blocks() as demo:
    gr.Markdown(
        """
        <style>
        .gr-button-secondary {
            width: 100px;
            height: 30px;
            padding: 5px;
        }
        .gr-row {
            display: flex;
            align-items: center;
            gap: 10px;
        }
        .gr-block {
            padding: 20px;
        }
        .gr-markdown p {
            font-size: 16px;
        }
        </style>
        <span style='font-family: Arial, sans-serif; font-size: 20px;'>Was this text written by <strong>human</strong> or <strong>AI</strong>?</span>
        <p style='font-family: Arial, sans-serif;'>Try detecting one of our sample texts:</p>
        """
    )
    
    with gr.Row():
        for sample in ["Machine-Generated", "Human-Written", "Machine-Humanized", "Machine - Polished"]:
            gr.Button(sample, variant="outline")

    with gr.Row():
        radio_button = gr.Radio([ 'Student Essay','Scientific Abstract'], label = 'Text Type', info = 'We have specialized models that work on domain-specific text.', value = 'Student Essay')

    with gr.Row():
        input_text = gr.Textbox(placeholder="Paste your text here...", label="", lines=10)
        file_input = gr.File(label="Upload File")

    #file_input = gr.File(label="", visible=False)  # Hide the actual file input
    
    with gr.Row():
        check_button = gr.Button("Check Origin", variant="primary")
        clear_button = gr.ClearButton([input_text, file_input, radio_button], variant='stop')
        #upload_button = gr.Button("Upload File", variant="secondary")
    
    out = gr.Textbox(label="OUTPUT", placeholder="", lines=2)
    clear_button.add(out)
    
    check_button.click(fn=update, inputs=[input_text, file_input, radio_button], outputs=out)
    #upload_button.click(lambda: None, inputs=[], outputs=[]).then(fn=update, inputs=[input_text, file_input], outputs=out)

    # Adding JavaScript to simulate file input click
    gr.Markdown(
        """
        <script>
        document.addEventListener("DOMContentLoaded", function() {
            const uploadButton = Array.from(document.getElementsByTagName('button')).find(el => el.innerText === "Upload File");
            if (uploadButton) {
                uploadButton.onclick = function() {
                    document.querySelector('input[type="file"]').click();
                };
            }
        });
        </script>
        """
    )

demo.launch(share=True)

